# QPU Tokens

Luna integrates with various quantum hardware providers, enabling seamless algorithm execution. To streamline your workflow, Luna securely stores your tokens, allowing you to reuse them across services. This lets you set your token once without needing to provide it for each individual run. Alternatively, you can provide a token inline for each call to quantum hardware if preferred.

Upon completing this tutorial, you will be able to:

1. Set your QPU token in Luna once for consistent reuse.
2. Distinguish between personal and organization-level tokens.
3. Manage, modify, and remove your QPU tokens.
4. Use QPU tokens to run algorithms on quantum hardware.

First, you'll need to import the necessary packages and initiate your session with Luna. You can use both a LunaSolve and a LunaQ session, as the tokens are shared by both services. In this example, we will use LunaSolve.

In [ ]:
# Load the Luna package
from luna_sdk import LunaSolve

# Initialize LunaSolve with your credentials
ls = LunaSolve(email="YOUREMAIL", password="YOURPASSWORD")

## Setting Your QPU Token

By storing your QPU token in Luna, you can seamlessly reuse it across different runs while running algorithms on quantum hardware. As a regular user, you can only set tokens for your personal account. As an admin, however, you can also configure tokens for your entire organization.

At the organizational level, you have the flexibility to assign quantum hardware access tokens, enabling users to utilize the hardware while preventing unauthorized viewing, modification, or deletion of the tokens.

To associate your account with an organization and gain administrative privileges, please contact us. Once you secure administrative access, you can start adding organization-level QPU tokens.

In this tutorial, we'll use IBM's hardware as an example. The process of setting tokens for other hardware providers is the same. You can find a complete list of available providers in our [quantum hardware providers documentation](TODO:Link to hardware documentation).

In [ ]:
# Set your personal token to access IBMs hardware
personal_token = ls.qpu_token.create(
    name="My Personal IBM Token",
    provider="ibm",
    token="<TOKEN>",
    token_type="personal"
)

# As an administrator you can also set your organization token to access IBMs hardware
organization_token = ls.qpu_token.create(
    name="My Organization IBM Token",
    provider="ibm",
    token="<TOKEN>",
    token_type="organization"
)

## Managing Your QPU Tokens

Luna makes it easy to manage all your stored QPU tokens. You can retrieve, edit, and delete your tokens. Note that only admins can perform these actions for organization-level tokens.

In [ ]:
# Retrieve a personal token
personal_token = ls.qpu_token.get(
    qpu_token_id=personal_token.id
)

print(personal_token)

# Retrieve an organization token (only for admins)
organization_token = ls.qpu_token.get(
    qpu_token_id=organization_token.id,
    token_type="organization"
)

print(organization_token)


In [ ]:
# Retrieve all tokens that are available to you
all_tokens = ls.qpu_token.get_all()

print(all_tokens)

In [ ]:
# Rename a QPU Token
renamed_token = ls.qpu_token.rename(
    qpu_token_id=personal_token.id,
    name="My Updated Personal Token"
)

print(renamed_token)

In [ ]:
# Delete a personal QPU Token
ls.qpu_token.delete(
    qpu_token_id=renamed_token.id
)

# Delete an organization QPU Token (only for admins)
ls.qpu_token.delete(
    qpu_token_id=organization_token.id,
    token_type="organization"
)

## Using QPU Tokens to Access Quantum Hardware

To access quantum hardware, you'll need a QPU token specific to the corresponding provider. By storing your QPU token in Luna, you only need to specify which token to use for hardware access.

In [ ]:
from luna_sdk.schemas.qpu_token import QpuToken, TokenProvider

# As an example, define a QUBO matrix
qubo_matrix = [
    [4, 0, 0, 0, -2],
    [0, -2, 0, 0, 0],
    [0, 0, 6, -3, 0],
    [0, 0, -3, 2, 0],
    [-2, 0, 0, 0, 5]
]

# Upload your QUBO to LunaSolve
optimization = ls.optimization.create_from_qubo(name="My QUBO", matrix=qubo_matrix)

# Solve the QUBO using QAOA and the least busy backend from IBM
job = ls.solution.create(
    optimization_id=optimization.id,
    solver_name="QAOA",
    provider="ibm",
    qpu_tokens=TokenProvider(
        ibm=QpuToken(
            source="personal",
            name="My IBM Token"
        )
    ),
    solver_parameters={"backend": "least_busy"}
)

Alternatively, you can provide an inline token that doesn't need to be stored in Luna.

In [ ]:
job = ls.solution.create(
    optimization_id=optimization.id,
    solver_name="QAOA",
    provider="ibm",
    qpu_tokens=TokenProvider(
        ibm=QpuToken(
            source="inline",
            token="<TOKEN>"
        )
    ),
    solver_parameters={"backend": "least_busy"}
)

In addition, you can also use environment variables for inline tokens. To do this, you need to set the appropriate environment variables. Below are the currently supported environment variables:

- `LUNA_IBM_TOKEN`
- `LUNA_DWAVE_TOKEN`
- `LUNA_QCTRL_TOKEN`
- `LUNA_FUJITSU_TOKEN`
- `LUNA_AWS_ACCESS_KEY`
- `LUNA_AWS_SECRET_ACCESS_KEY`

If you are unsure how to set environment variables, please refer to the [Luna Environment Variables](https://docs.aqarios.com/get-started#luna-environment-variables) section on the [Get Started](https://docs.aqarios.com/get-started) page.

Once you set the `LUNA_IBM_TOKEN` environment variable as shown in the code above, you can omit the `qpu_tokens` parameter in your operations. The token from your environment variable will be used automatically.

In [ ]:
job = ls.solution.create(
    optimization_id=optimization.id,
    solver_name="QAOA",
    provider="ibm",
    solver_parameters={"backend": "least_busy"}
)

Note that when using the `qpu_tokens` parameter, this parameter will be prioritized over QPU tokens stored in environment variables.